<a href="https://colab.research.google.com/github/sihyeon3523/Six_of_cells/blob/modeling/KoBERT_keras_2_del_neutral.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
macfrom IPython.display import clear_output 

!pip install transformers==4.8.2
!pip install sentencepiece==0.1.96
!pip install tensorflow_addons

clear_output()

In [ ]:
import sklearn
import tensorflow
import transformers
import tensorflow_addons

print(sklearn.__version__) # 1.0.2
print(tensorflow.__version__) # 2.8.0
print(transformers.__version__) # 4.8.2
print(tensorflow_addons.__version__) # 0.16.1

import sentencepiece

1.0.2
2.8.0
4.8.2
0.17.0


In [ ]:
import pandas as pd
import numpy as np

import os
import re
import pickle 
import dill # for saving a function as a file(.pkl)
import logging # for changing the tf's logging level
import urllib.request
from tqdm import tqdm

from sklearn import model_selection
from sklearn.metrics import accuracy_score

import tensorflow as tf
import tensorflow_addons as tfa # for using Rectified-Adam optimizer (instead of Adam optimizer) 
from tensorflow.keras import layers, initializers, losses, optimizers, metrics, callbacks 

import transformers
from transformers import TFBertModel # BertTokenizer 제외

import sentencepiece as spm

In [ ]:
# Random seed 고정
tf.random.set_seed(1234)
np.random.seed(1234)

# Transformers logging level 변경 (WARNING -> ERROR) @ https://huggingface.co/transformers/main_classes/logging.html
transformers.logging.set_verbosity(transformers.logging.ERROR)

# Tensorflow logging level 변경 
tf.get_logger().setLevel(logging.ERROR)

# load data

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
df=pd.read_csv("/content/drive/MyDrive/final/new_train_del_neu.csv",index_col=0)

In [ ]:
df

index                                           Sentence label
0           0               아 진짜! 사무실에서 피지 말라니깐! 간접흡연이 얼마나 안좋은데!    분노
1           1       그럼 직접흡연하는 난 얼마나 안좋겠니? 안그래? 보면 꼭... 지 생각만 하고.    혐오
2           6                                     그걸 내가 어떻게 알아요!    분노
3          14                               동사무소에서 인구조사 나왔니? 지금.    분노
4          16                                    나? ... 나보고 하라고?    놀람
...       ...                                                ...   ...
61694  113563               솔직히 예보 제대로 못하는 데 세금이라도 아끼게 그냥 폐지해라..    혐오
61695  113564                                        재미가 없으니 망하지    혐오
61696  113565  공장 도시락 비우생적임 아르바이트했는데 화장실가성 손도 않씯고 재료 담고 바닥 떨어...    혐오
61697  113566               코딱지 만한 나라에서 지들끼리 피터지게 싸우는 센징 클래스 ㅉㅉㅉ    혐오
61698  113567               와이프도 그렇고 댓글 다 볼텐데 이휘재 좀 하차 하라고 전해주세요    혐오

[61699 rows x 3 columns]

In [ ]:
df[ df['Sentence'].duplicated(keep=False) == True ].sort_values('Sentence')

index                            Sentence label
1062    2969   ... 그래. 알았어. 그만 하자. 내가 잘못했어. 그만해.    슬픔
63       240   ... 그래. 알았어. 그만 하자. 내가 잘못했어. 그만해.    슬픔
1014    2768     ... 너 오늘 유난히 대답 잘 한다? 라임 맞춰가면서.    혐오
15        39     ... 너 오늘 유난히 대답 잘 한다? 라임 맞춰가면서.    혐오
39300  86339                       7로 나온다든데 아니었나    놀람
...      ...                                 ...   ...
8349   33967                                  후…    분노
12764  56677                  휴가 첫날부터 하루종일 비가 와.    분노
15399  59871                  휴가 첫날부터 하루종일 비가 와.    분노
16837  61604                           휴가인데 이러네.    분노
17519  62433                           휴가인데 이러네.    분노

[5072 rows x 3 columns]

In [ ]:
df["label"].value_counts()

분노    12556
놀람    12519
행복    11615
슬픔    10087
혐오     7970
공포     6952
Name: label, dtype: int64

In [ ]:
df = df.drop_duplicates('Sentence') 
df = df.reset_index(drop=True)

In [ ]:
df["label"].value_counts()

분노    12106
놀람    11320
행복    10654
슬픔     9384
혐오     7577
공포     6708
Name: label, dtype: int64

In [ ]:
print('중복 제거 후 전체 리뷰 수 :', len(df))

중복 제거 후 전체 리뷰 수 : 57749


In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 57749 entries, 0 to 57748
Data columns (total 3 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   index     57749 non-null  int64 
 1   Sentence  57749 non-null  object
 2   label     57749 non-null  object
dtypes: int64(1), object(2)
memory usage: 1.3+ MB


In [ ]:
del df["index"]

Undersampling


In [ ]:
# df_mid=df[df["label"] == "중립"]
# df_not_mid=df[df["label"] != "중립"]

In [ ]:
# df_mid

Sentence label
2                                        손님 왔어요.    중립
3                                        손님? 누구?    중립
4                                 몰라요. 팀장님 친구래요.    중립
5                                   내 친구? 친구 누구?    중립
7                                 그래서... 무슨 일 해?    중립
...                                          ...   ...
94381                    호텔 CCTV ,차량 블랙박스 조사해보세요    중립
94382  ㅋㅋㅋㅋ 어제 누가 헬쥐졌으니 3시에 올라올거라 하더니 4시....ㅋㅋㅋㅋ    중립
94383                     공격에선 체력저하로 세컨볼 획득 안됨..    중립
94384                   한화가 삼성과 KT는 기본으로 깔고 가겠네.    중립
94385             실제 저런몸이 오히려 대한민국 여자들에게 인기가 많다.    중립

[48282 rows x 2 columns]

In [ ]:
# df_not_mid

Sentence label
0                    아 진짜! 사무실에서 피지 말라니깐! 간접흡연이 얼마나 안좋은데!    분노
1            그럼 직접흡연하는 난 얼마나 안좋겠니? 안그래? 보면 꼭... 지 생각만 하고.    혐오
6                                          그걸 내가 어떻게 알아요!    분노
14                                   동사무소에서 인구조사 나왔니? 지금.    분노
16                                        나? ... 나보고 하라고?    놀람
...                                                   ...   ...
105807               솔직히 예보 제대로 못하는 데 세금이라도 아끼게 그냥 폐지해라..    혐오
105808                                        재미가 없으니 망하지    혐오
105809  공장 도시락 비우생적임 아르바이트했는데 화장실가성 손도 않씯고 재료 담고 바닥 떨어...    혐오
105810               코딱지 만한 나라에서 지들끼리 피터지게 싸우는 센징 클래스 ㅉㅉㅉ    혐오
105811               와이프도 그렇고 댓글 다 볼텐데 이휘재 좀 하차 하라고 전해주세요    혐오

[57530 rows x 2 columns]

In [ ]:
# # random undersampling
# df_mid=df_mid.sample(frac=0.25,random_state=1004)

In [ ]:
# df=pd.concat([df_mid,df_not_mid])

In [ ]:
df

Sentence label
37107                                         오늘 접대가 있어서~    중립
93748                                 케바케 오십년전에도 쓰던 말인데..    중립
24018                                              할망구같아.    중립
91429                   이거 해결 안되면 삼성은 큰 위기에 빠질 것은 불보듯 뻔하다    중립
65558                           나 오늘 짭새새끼들이 몰려있길래 구경갔다왔다.    중립
...                                                   ...   ...
105807               솔직히 예보 제대로 못하는 데 세금이라도 아끼게 그냥 폐지해라..    혐오
105808                                        재미가 없으니 망하지    혐오
105809  공장 도시락 비우생적임 아르바이트했는데 화장실가성 손도 않씯고 재료 담고 바닥 떨어...    혐오
105810               코딱지 만한 나라에서 지들끼리 피터지게 싸우는 센징 클래스 ㅉㅉㅉ    혐오
105811               와이프도 그렇고 댓글 다 볼텐데 이휘재 좀 하차 하라고 전해주세요    혐오

[69600 rows x 2 columns]

In [ ]:
df.value_counts(["label"])

label
분노       12106
놀람       11320
행복       10654
슬픔        9384
혐오        7577
공포        6708
dtype: int64

In [ ]:
emotion_mapping = {"분노":0, "놀람":1, "행복":2, "슬픔":3, "혐오":4,"공포":5 }

df['label'] = df['label'].map(emotion_mapping)

In [ ]:
df.value_counts(["label"])

label
0        12106
1        11320
2        10654
3         9384
4         7577
5         6708
dtype: int64

In [ ]:
df

Sentence  label
0                   아 진짜! 사무실에서 피지 말라니깐! 간접흡연이 얼마나 안좋은데!      0
1           그럼 직접흡연하는 난 얼마나 안좋겠니? 안그래? 보면 꼭... 지 생각만 하고.      4
2                                         그걸 내가 어떻게 알아요!      0
3                                   동사무소에서 인구조사 나왔니? 지금.      0
4                                        나? ... 나보고 하라고?      1
...                                                  ...    ...
57744               솔직히 예보 제대로 못하는 데 세금이라도 아끼게 그냥 폐지해라..      4
57745                                        재미가 없으니 망하지      4
57746  공장 도시락 비우생적임 아르바이트했는데 화장실가성 손도 않씯고 재료 담고 바닥 떨어...      4
57747               코딱지 만한 나라에서 지들끼리 피터지게 싸우는 센징 클래스 ㅉㅉㅉ      4
57748               와이프도 그렇고 댓글 다 볼텐데 이휘재 좀 하차 하라고 전해주세요      4

[57749 rows x 2 columns]

In [ ]:
train_x, test_x, train_y, test_y = model_selection.train_test_split(df['Sentence'], df['label'], 
                                                                    test_size=0.3, 
                                                                    random_state=42) 

# preprocessing

In [ ]:
#KoBERT 불러오기
!git clone https://github.com/monologg/KoBERT-Transformers.git
!mv KoBERT-Transformers/kobert_transformers/tokenization_kobert.py /content
clear_output() # clear the output

#토크나이저 생성
from tokenization_kobert import KoBertTokenizer 

tokenizer = KoBertTokenizer.from_pretrained('monologg/kobert')

Downloading:   0%|          | 0.00/371k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/77.8k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/51.0 [00:00<?, ?B/s]

In [ ]:
df['Sentence'].str.len().sort_values(ascending=False)[:5]

37859    299
51427    298
57324    295
55745    261
8710     209
Name: Sentence, dtype: int64

In [ ]:
len(tokenizer.tokenize(df['Sentence'][37859]))

75

In [ ]:
df['Sentence'][37859]

'쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기 쓰레기'

In [ ]:
len(tokenizer.tokenize(df['Sentence'][51427]))

292

In [ ]:
len(tokenizer.tokenize(df['Sentence'][51427]))

292

In [ ]:
SEQ_LEN = 300

token_ids = []
token_segments = []
token_masks = []

train_labels = []

for idx in tqdm(range(len(train_x))):

  # 'Sentence'칼럼에서 0번째 행~ 꺼내오기
  train_sentence = train_x.iloc[idx]
  print(train_sentence) 

  # 특수문자 제거
  cleaned_sentence = re.sub("[^\s0-9a-zA-Zㄱ-ㅎㅏ-ㅣ가-힣]", "", train_sentence)
  print(cleaned_sentence)

  # 토큰화 + 토큰별 시퀀스번호 부여 + 패딩
  encoded_dict = tokenizer.encode_plus(text = cleaned_sentence,
                                       padding='max_length',
                                       truncation=True,
                                       max_length=SEQ_LEN
                                       )
  
  #'input_ids', 'token_type_ids', 'attention_mask'
  token_ids.append(encoded_dict['input_ids'])
  token_masks.append(encoded_dict['attention_mask'])
  token_segments.append(encoded_dict['token_type_ids'])

  train_labels.append(train_y.iloc[idx])


train_inputs = (np.array(token_ids), np.array(token_masks), np.array(token_segments))
train_labels = np.array(train_labels)

  1%|          | 466/40424 [00:00<00:17, 2342.64it/s]

  걱정이 많치요..
  걱정이 많치요
와 진짜 합의 없이 싹다 처벌해주길!!
와 진짜 합의 없이 싹다 처벌해주길
예전남친은 이제 제생각도 안나고 그렇겟죠..
예전남친은 이제 제생각도 안나고 그렇겟죠
힘들어도 얼른 방을 치워야 할 것 같아. 이 냄새 때문에 벌레가 생길 것 같아.
힘들어도 얼른 방을 치워야 할 것 같아 이 냄새 때문에 벌레가 생길 것 같아
닥터스에서 젤루 매력 터지는 캐릭터~
닥터스에서 젤루 매력 터지는 캐릭터
 예전회사들도 퇴사한다고하면 다니는 동안 계속 눈치주고 그래서 말하기가 무서운데..
 예전회사들도 퇴사한다고하면 다니는 동안 계속 눈치주고 그래서 말하기가 무서운데
보정ㅋㅋㅋㅋ 뇌를 좀 보정해라 ㅋㅋ
보정ㅋㅋㅋㅋ 뇌를 좀 보정해라 ㅋㅋ
확실한건 역사책에 네이름은 기록될듯하다 희대의 정치악마
확실한건 역사책에 네이름은 기록될듯하다 희대의 정치악마
친구가 추천한 주식 샀는데 올라갈 기미가 안 보여.
친구가 추천한 주식 샀는데 올라갈 기미가 안 보여
역시 양준혁이란 이름에는 3할타율과 폭발적인 장타와 이를 악 물고 하고 베이스런닝은 정말 멋있습니다...
역시 양준혁이란 이름에는 3할타율과 폭발적인 장타와 이를 악 물고 하고 베이스런닝은 정말 멋있습니다
지옥에 불반도가 현실이되네ㅋㅋ
지옥에 불반도가 현실이되네ㅋㅋ
세계 곳곳에 또라이들이 많네
세계 곳곳에 또라이들이 많네
사지마라 안사면되지
사지마라 안사면되지
살인자 같이 생겼네
살인자 같이 생겼네
저 말 무시하고 그냥 강제구인 하세요.
저 말 무시하고 그냥 강제구인 하세요
나 해피랑 산책하다 정말 깜짝 놀랐어.
나 해피랑 산책하다 정말 깜짝 놀랐어
무섭지. 엄청 무서워죽겠어.
무섭지 엄청 무서워죽겠어
왠지 불안한 건 나뿐인가?
왠지 불안한 건 나뿐인가
연아선수덕에 저를 비롯한 많은 사람들이 너무도 행복한 시간을 보냈어요
연아선수덕에 저를 비롯한 많은 사람들이 너무도 행복한 시간을 보냈어요
에휴 저것들 작살내야 하는데..
에휴 저것들 작살내야 하는데
정말 많은 사람들이 놀랐지. 사람들이 소리를 지

  2%|▏         | 701/40424 [00:00<00:18, 2163.67it/s]

내 상각도 안할텐데.
내 상각도 안할텐데
갑자기 사귀자네요.
갑자기 사귀자네요
 진짜 기막힐 노릇이다..
 진짜 기막힐 노릇이다
죽일 놈 맞네. 지금까지 데리고 살아 준 게 대단하다. 당신이 왜 이렇게 드세졌는지 알겠다..
죽일 놈 맞네 지금까지 데리고 살아 준 게 대단하다 당신이 왜 이렇게 드세졌는지 알겠다
보건행정아님간호행정갈라하는대..
보건행정아님간호행정갈라하는대
피해랄 것도 없고 그냥 내가 잠을 못 잘 것 같긴 해.
피해랄 것도 없고 그냥 내가 잠을 못 잘 것 같긴 해
다른 직원들한테는 친절하게 하면서 나한테만 짜증 내고 뭐라고 하니까 화가 나서 그래.
다른 직원들한테는 친절하게 하면서 나한테만 짜증 내고 뭐라고 하니까 화가 나서 그래
아따 오늘도 전라도에서 버스로 상경많이하겠냉
아따 오늘도 전라도에서 버스로 상경많이하겠냉
개념없는 쓰레기들... 고작 게임하나에 목숨거네...
개념없는 쓰레기들 고작 게임하나에 목숨거네
아니 베터리 무상교체 프로그램 실행중이라면서 내거는 정상이라고 그냥 빠꾸시키던데 뭐냐 ㅡㅡ
아니 베터리 무상교체 프로그램 실행중이라면서 내거는 정상이라고 그냥 빠꾸시키던데 뭐냐 ㅡㅡ
너 지금 뭐하자는 거야?
너 지금 뭐하자는 거야
그냥 다짜르고 알파고 도입
그냥 다짜르고 알파고 도입
인플루언서가 이벤트 하는 것을 발견해서 신청했더니 당첨됐어.
인플루언서가 이벤트 하는 것을 발견해서 신청했더니 당첨됐어
어? 왔냐?
어 왔냐
올해의 부실대는 이대인가요?
올해의 부실대는 이대인가요
미친 아줌마 둘이서 망친나라.정상적인 아줌마들이 구하네
미친 아줌마 둘이서 망친나라정상적인 아줌마들이 구하네
코로나땜에 밖에 나가지도 못하고 집에서 일만 하고 있어.
코로나땜에 밖에 나가지도 못하고 집에서 일만 하고 있어
 친구들은 이쁘다고 그러는데 힘드네요
 친구들은 이쁘다고 그러는데 힘드네요
오늘도 견찰은 열심히 세금걷습니다. 왈왈
오늘도 견찰은 열심히 세금걷습니다 왈왈
시간이 해결해준다는 뻔한말도 결국 맞는말이에요?
시간이 해결해준다는 뻔한말도 결국 맞는말이에요

  2%|▏         | 919/40424 [00:00<00:20, 1897.72it/s]

...


다행히 무슨 일이 생기기 전에 옆에 지나가던 아저씨가 잡아주셨어
바리바리 양세바리 쵝오!!
바리바리 양세바리 쵝오
아. 여행 너무 좋지. 진짜 그냥 하나하나 다 해버려야겠다! 기대돼!
아 여행 너무 좋지 진짜 그냥 하나하나 다 해버려야겠다 기대돼
친구가 오늘 생일인데 선물을 뭘사줘야할지 너무 고민이에요ㅜㅜ
친구가 오늘 생일인데 선물을 뭘사줘야할지 너무 고민이에요ㅜㅜ
심한건 아닌데 이전까진 워낙 입냄새가 안나던 친구이다 보니까 좀 신경이 쓰입니다.
심한건 아닌데 이전까진 워낙 입냄새가 안나던 친구이다 보니까 좀 신경이 쓰입니다
자연의 재앙앞에서 인간은 무릎을끓는다
자연의 재앙앞에서 인간은 무릎을끓는다
 오늘 제  문자와 전화까지 모두 안받네요.
 오늘 제  문자와 전화까지 모두 안받네요
이사람 롯데있을때도 잘던졌었나???
이사람 롯데있을때도 잘던졌었나
니들 하는거 보니까...진심...무섭다..
니들 하는거 보니까진심무섭다
담화 수준 좀 보소...
담화 수준 좀 보소
에이 그러게 250만원짜린데 설마 문제가 있겠어?
에이 그러게 250만원짜린데 설마 문제가 있겠어
어? 괜찮아. 아가씨, 참 고맙네. 아가씨도 다칠 뻔했는데 괜찮아?
어 괜찮아 아가씨 참 고맙네 아가씨도 다칠 뻔했는데 괜찮아
 삼성의 지나친 스펙 지상주의의 결과다.
 삼성의 지나친 스펙 지상주의의 결과다
나 너무 우울해, 지금.
나 너무 우울해 지금
그 여자들은 정말 운도 좋지.
그 여자들은 정말 운도 좋지
그러게 말이야.
그러게 말이야
경고먹을까 고민0
경고먹을까 고민0
벌레가 나왔는데 이거 당연한 거지!
벌레가 나왔는데 이거 당연한 거지
어딨어?
어딨어
다이어트전에는 165에 58kg이었어요
다이어트전에는 165에 58kg이었어요
특위의는 위증한 애들(전부) 걍 다 고발 올인
특위의는 위증한 애들전부 걍 다 고발 올인
야구라는 스포츠는 망하게 놔두고 저딴승마에는 200억 ㄷ
야구라는 스포츠는 망하게 놔두고 저딴승마에는 200억 ㄷ
거부할수없는 여왕의 품격이긴하지 허허
거부할수없는 여왕의 품격이긴

100%|█████████▉| 40341/40424 [00:42<00:00, 1027.95it/s]

안녕하세요~ 박보검입니다~^^♡
안녕하세요 박보검입니다
걸그룹대첩보다 이게 훨씬 더 재미있다
걸그룹대첩보다 이게 훨씬 더 재미있다
역시 돈이 있고 봐야하는거야 모야
역시 돈이 있고 봐야하는거야 모야
아니 얘가 얘가! 무슨 말을 하는거야?
아니 얘가 얘가 무슨 말을 하는거야
하루가 다르게 자라지? 
하루가 다르게 자라지 
한밤중에 말도 없이요? 것도 맨발로요? 돈도 안 갖고? 핸드폰도 없이?
한밤중에 말도 없이요 것도 맨발로요 돈도 안 갖고 핸드폰도 없이
얼굴값 못하시는 분ㅜㅜ
얼굴값 못하시는 분ㅜㅜ
나는 재미있는 영화나 신나는 음악이 좋더라고.
나는 재미있는 영화나 신나는 음악이 좋더라고
악재를 털어?ㅋㅋㅋㅋㅋㅋㅋㅋㅋ
악재를 털어ㅋㅋㅋㅋㅋㅋㅋㅋㅋ
그것때문에 운동하는 거지.
그것때문에 운동하는 거지
뭐? 얼굴.. 하..
뭐 얼굴 하
아 몸은 괜찮은데, 어떻게 할까 모르겠네.
아 몸은 괜찮은데 어떻게 할까 모르겠네
고마워. 니 조언이 도움이 되었어.
고마워 니 조언이 도움이 되었어
안좋아하기는!
안좋아하기는
구매해야되겠어. 좋은 거 있으면 추천해줘.
구매해야되겠어 좋은 거 있으면 추천해줘
그래두 오랜만에 외식인데.
그래두 오랜만에 외식인데
간경화에 약이 어딨어요! 스트레스를 안 받아야지 스트레스를!
간경화에 약이 어딨어요 스트레스를 안 받아야지 스트레스를
완전히 끝났어. 속이 아주 시원해. 그 동안 열심히 일을 했거든. 쉬지도 못하고 너무 힘들었어.
완전히 끝났어 속이 아주 시원해 그 동안 열심히 일을 했거든 쉬지도 못하고 너무 힘들었어
너한테 그렇게 매달렸는데 넌 싫다고했어
너한테 그렇게 매달렸는데 넌 싫다고했어
허벌나게 사귀어 불고 헤어지는구만유
허벌나게 사귀어 불고 헤어지는구만유
리콜했는데 별 이미지 타격이 없나봐???
리콜했는데 별 이미지 타격이 없나봐
무슨 피장파장이요? 누가 먼저 시작했는데 이제 와서 그런 말씀이세요?
무슨 피장파장이요 누가 먼저 시작했는데 이제 와서 그런 말씀이세요
조만간 김신욱 보려 스카웃터들 한국 방문할듯ㅎ
조만간 김신욱 보려 스카

100%|██████████| 40424/40424 [00:42<00:00, 949.77it/s] 


얼굴 탱탱해서 언넘한테 시집 갈려고 ㅋㅋ
약 올리냐? 주 후반부터 꺾인다며 이새끼들아
약 올리냐 주 후반부터 꺾인다며 이새끼들아
여린 소녀에게 그런 실례의 말씀을!
여린 소녀에게 그런 실례의 말씀을
냄새도 없애고 방을 치우려면 너무 힘들긴 하지만 얼른 청소를 하는 게 나을 것 같아.
냄새도 없애고 방을 치우려면 너무 힘들긴 하지만 얼른 청소를 하는 게 나을 것 같아
사사건건 잘못되기를바라고 자기나라를비하하는 못난인간들 왜이리많냐.
사사건건 잘못되기를바라고 자기나라를비하하는 못난인간들 왜이리많냐


In [ ]:
train_inputs

(array([[   2,  880, 7096, ...,    1,    1,    1],
        [   2,  517, 6983, ...,    1,    1,    1],
        [   2, 3412, 5666, ...,    1,    1,    1],
        ...,
        [   2, 3298, 6133, ...,    1,    1,    1],
        [   2,  517, 5684, ...,    1,    1,    1],
        [   2, 2573, 6495, ...,    1,    1,    1]]),
 array([[1, 1, 1, ..., 0, 0, 0],
        [1, 1, 1, ..., 0, 0, 0],
        [1, 1, 1, ..., 0, 0, 0],
        ...,
        [1, 1, 1, ..., 0, 0, 0],
        [1, 1, 1, ..., 0, 0, 0],
        [1, 1, 1, ..., 0, 0, 0]]),
 array([[0, 0, 0, ..., 0, 0, 0],
        [0, 0, 0, ..., 0, 0, 0],
        [0, 0, 0, ..., 0, 0, 0],
        ...,
        [0, 0, 0, ..., 0, 0, 0],
        [0, 0, 0, ..., 0, 0, 0],
        [0, 0, 0, ..., 0, 0, 0]]))

In [ ]:
set(train_labels)

{0, 1, 2, 3, 4, 5}

# modeling

In [ ]:
def create_model(max_length=300):

    bert_base_model = TFBertModel.from_pretrained("monologg/kobert", from_pt=True) 

    input_token_ids   = layers.Input((max_length,), dtype=tf.int32, name='input_token_ids')   # tokens_tensor
    input_masks       = layers.Input((max_length,), dtype=tf.int32, name='input_masks')       # masks_tensor
    input_segments    = layers.Input((max_length,), dtype=tf.int32, name='input_segments')    # segments_tensor  

    bert_outputs = bert_base_model([input_token_ids, input_masks, input_segments]) 
    

    bert_outputs = bert_outputs[1] # ('pooler_output', <KerasTensor: shape=(None, 768) dtype=float32 (created by layer 'tf_bert_model')>)
    bert_outputs = layers.Dropout(0.2)(bert_outputs)
    final_output = layers.Dense(units=6, activation='softmax', kernel_initializer=initializers.TruncatedNormal(stddev=0.02), name="classifier")(bert_outputs)

    model = tf.keras.Model(inputs=[input_token_ids, input_masks, input_segments], 
                        outputs=final_output)

    model.compile(optimizer=tfa.optimizers.RectifiedAdam(learning_rate=1e-5, weight_decay=0.0025, warmup_proportion=0.05),
                  loss=losses.SparseCategoricalCrossentropy(), 
                  metrics=[metrics.SparseCategoricalAccuracy()])
    
    return model

In [ ]:
# TPU setting

resolver = tf.distribute.cluster_resolver.TPUClusterResolver(tpu='grpc://' + os.environ['COLAB_TPU_ADDR'])
tf.config.experimental_connect_to_cluster(resolver)
tf.tpu.experimental.initialize_tpu_system(resolver)
print("\nAll devices: ", tf.config.list_logical_devices('TPU'))

strategy = tf.distribute.TPUStrategy(resolver)

with strategy.scope(): 
    model = create_model(max_length=300)

INFO:absl:Entering into master device scope: /job:worker/replica:0/task:0/device:CPU:0



All devices:  [LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:0', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:1', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:2', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:3', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:4', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:5', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:6', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:7', device_type='TPU')]


Downloading:   0%|          | 0.00/426 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/369M [00:00<?, ?B/s]

# Train

In [ ]:
# Checkpoint setting for saving the best model
from google.colab import drive
drive.mount('/gdrive')

checkpoint_path = '/gdrive/MyDrive/final/colab_data/saved_models/'

if not os.path.exists(checkpoint_path):
    os.makedirs(checkpoint_path)

callback_checkpoint = callbacks.ModelCheckpoint(filepath=checkpoint_path + 'best_bert_weights.h5', 
                                                monitor='val_sparse_categorical_accuracy',
                                                save_best_only=True, 
                                                save_weights_only = True, 
                                                verbose=1) 
                                                
# Early-stopping for preventing the overfitting
callback_earlystop = callbacks.EarlyStopping(monitor='val_sparse_categorical_accuracy', 
                                             min_delta=0.0001, 
                                             patience=5) 

Mounted at /gdrive


In [ ]:
history = model.fit(train_inputs, train_labels, validation_split=0.2,
                    epochs=10, batch_size=200,
                    verbose=1,
                    callbacks=[callback_checkpoint, callback_earlystop])

Epoch 1/10


INFO:absl:TPU has inputs with dynamic shapes: [<tf.Tensor 'Const:0' shape=() dtype=int32>, <tf.Tensor 'cond/Identity:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_8:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_16:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_24:0' shape=(None,) dtype=int64>]
INFO:absl:TPU has inputs with dynamic shapes: [<tf.Tensor 'Const:0' shape=() dtype=int32>, <tf.Tensor 'cond/Identity:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_8:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_16:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_24:0' shape=(None,) dtype=int64>]


162/162 [==============================] - ETA: 0s - loss: 1.7672 - sparse_categorical_accuracy: 0.2327

INFO:absl:TPU has inputs with dynamic shapes: [<tf.Tensor 'Const:0' shape=() dtype=int32>, <tf.Tensor 'cond/Identity:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_8:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_16:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_24:0' shape=(None,) dtype=int64>]



Epoch 1: val_sparse_categorical_accuracy improved from -inf to 0.31478, saving model to /gdrive/MyDrive/final/colab_data/saved_models/best_bert_weights.h5
162/162 [==============================] - 268s 944ms/step - loss: 1.7672 - sparse_categorical_accuracy: 0.2327 - val_loss: 1.7122 - val_sparse_categorical_accuracy: 0.3148
Epoch 2/10
162/162 [==============================] - ETA: 0s - loss: 1.6264 - sparse_categorical_accuracy: 0.3526
Epoch 2: val_sparse_categorical_accuracy improved from 0.31478 to 0.41274, saving model to /gdrive/MyDrive/final/colab_data/saved_models/best_bert_weights.h5
162/162 [==============================] - 80s 495ms/step - loss: 1.6264 - sparse_categorical_accuracy: 0.3526 - val_loss: 1.4963 - val_sparse_categorical_accuracy: 0.4127
Epoch 3/10
162/162 [==============================] - ETA: 0s - loss: 1.4228 - sparse_categorical_accuracy: 0.4533
Epoch 3: val_sparse_categorical_accuracy improved from 0.41274 to 0.50105, saving model to /gdrive/MyDrive/fina

# Evaluate

In [ ]:
SEQ_LEN = 300 # 최대 token 개수 이상의 값으로 임의로 설정

token_ids =[]
token_masks =[]
token_segments =[]

test_labels = []


for idx in tqdm(range(len(test_x))):

    test_sentence = test_x.iloc[idx]
    
    # 특수문자 제거
    cleaned_sentence = re.sub("[^\s0-9a-zA-Zㄱ-ㅎㅏ-ㅣ가-힣]", "", test_sentence) 
    
    # Tokenizing / Tokens to sequence numbers / Padding
    encoded_dict = tokenizer.encode_plus(text=cleaned_sentence,
                                         padding='max_length', 
                                         truncation=True,
                                         max_length=SEQ_LEN)
    
    token_ids.append(encoded_dict['input_ids']) # tokens_tensor
    token_masks.append(encoded_dict['attention_mask']) # masks_tensor
    token_segments.append(encoded_dict['token_type_ids']) # segments_tensor

    test_labels.append(test_y.iloc[idx])


test_inputs = (np.array(token_ids), np.array(token_masks), np.array(token_segments))
test_labels = np.array(test_labels)

100%|██████████| 17325/17325 [00:05<00:00, 3091.35it/s]


In [ ]:
model.load_weights(filepath=checkpoint_path + 'best_bert_weights.h5') # Load the best model's weights from checkpoint file

preds = model.predict(test_inputs)
preds = tf.argmax(preds, axis=1)

print("Accuracy: ",accuracy_score(preds, test_labels))

INFO:absl:TPU has inputs with dynamic shapes: [<tf.Tensor 'Const:0' shape=() dtype=int32>, <tf.Tensor 'cond/Identity:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_8:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_16:0' shape=(None, 300) dtype=int64>]


Accuracy:  0.6224531024531025


In [ ]:
from sklearn.metrics import precision_score , recall_score , confusion_matrix, classification_report

#target_names = ['Neutral','Positive','Negative']
target_names = ['분노','놀람','행복',"슬픔","혐오","공포"] # {"분노":0, "놀람":1, "행복":2, "슬픔":3, "혐오":4,"공포":5 }

precision = precision_score(test_labels, preds,average= "macro")
recall = recall_score(test_labels, preds,average= "macro")

print("< Confusion Matrix >\n\n",confusion_matrix(test_labels, preds))
print("\n")
print("< Classification Report >\n\n",classification_report(test_labels, preds, target_names=target_names))

< Confusion Matrix >

 [[2620  331   72  220  309   97]
 [ 557 2152  173  216  139  239]
 [ 166  320 2406  214   67   36]
 [ 385  211  112 1668   60  293]
 [ 940  259   73  127  754   88]
 [ 168  292   25  305   47 1184]]


< Classification Report >

               precision    recall  f1-score   support

          분노       0.54      0.72      0.62      3649
          놀람       0.60      0.62      0.61      3476
          행복       0.84      0.75      0.79      3209
          슬픔       0.61      0.61      0.61      2729
          혐오       0.55      0.34      0.42      2241
          공포       0.61      0.59      0.60      2021

    accuracy                           0.62     17325
   macro avg       0.63      0.60      0.61     17325
weighted avg       0.63      0.62      0.62     17325



# Save Model

In [ ]:
from google.colab import drive
drive.mount('/gdrive')


data_path = '/gdrive/MyDrive/final/colab_data/temp_data/' 

if not os.path.exists(data_path): 
    os.makedirs(data_path)


with open(data_path + 'model_BERTfunction_v1.pkl', 'wb') as f:
    pickle.dump(dill.dumps(create_model), f) # use dill to pickle a function (https://j.mp/3CeSIzP & https://j.mp/3AaXxYW)

with open(data_path + 'tokenizer-bert.pkl', 'wb') as f:
    pickle.dump(tokenizer, f)     

Drive already mounted at /gdrive; to attempt to forcibly remount, call drive.mount("/gdrive", force_remount=True).


Load

In [ ]:
!pip install transformers==4.8.2
!pip install tensorflow_addons

import pandas as pd
import numpy as np

import re
import os
import pickle 
import dill # for saving a function as a file
import logging # for changing the tf's logging level
from IPython.display import clear_output 

import tensorflow as tf
import tensorflow_addons as tfa
from tensorflow.keras import layers, initializers, losses, optimizers, metrics 

import transformers
from transformers import TFBertModel 

# 이번 실습에서 추가되었습니다
!pip install sentencepiece==0.1.96
import sentencepiece as spm 
!git clone https://github.com/monologg/KoBERT-Transformers.git 
!mv KoBERT-Transformers/kobert_transformers/tokenization_kobert.py /content 
from tokenization_kobert import KoBertTokenizer 

# Tensorflow logging level 변경 
tf.get_logger().setLevel(logging.ERROR)

# clear the output after the installation
clear_output() 

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import dill 
import pickle 

In [ ]:
!git clone https://github.com/monologg/KoBERT-Transformers.git 
!mv KoBERT-Transformers/kobert_transformers/tokenization_kobert.py /content 
from tokenization_kobert import KoBertTokenizer 

fatal: destination path 'KoBERT-Transformers' already exists and is not an empty directory.
mv: cannot stat 'KoBERT-Transformers/kobert_transformers/tokenization_kobert.py': No such file or directory


In [ ]:
# 1) Load the Model-builder function
with open("/content/drive/MyDrive/final/colab_data/temp_data/model_BERTfunction_v1.pkl", 'rb') as f: # 이번 실습에서 변경되었습니다
    create_model = dill.loads(pickle.load(f)) # use dill to pickle a python function

In [ ]:
# 2) Load the Bert-tokenizer 
with open("/content/drive/MyDrive/final/colab_data/temp_data/tokenizer-bert.pkl", 'rb') as f:
    tokenizer = pickle.load(f) 

OSError: ignored

In [ ]:
resolver = tf.distribute.cluster_resolver.TPUClusterResolver(tpu='grpc://' + os.environ['COLAB_TPU_ADDR'])
tf.config.experimental_connect_to_cluster(resolver)
tf.tpu.experimental.initialize_tpu_system(resolver)
strategy = tf.distribute.TPUStrategy(resolver) # Obsolete : tf.distribute.experimental.TPUStrategy()

with strategy.scope(): 
    model = create_model(max_length=300) 

In [ ]:
checkpoint_path = '/content/drive/MyDrive/final/colab_data/saved_models/'
model.load_weights(filepath=checkpoint_path + 'best_bert_weights.h5')

In [ ]:
def predict_sentiment(sentence, tokenizer, model):
    
    SEQ_LEN = 300 

    # Tokenizing / Tokens to sequence numbers / Padding
    encoded_dict = tokenizer.encode_plus(text=re.sub("[^\s0-9a-zA-Zㄱ-ㅎㅏ-ㅣ가-힣]", "", sentence),
                                         padding='max_length', 
                                         truncation = True,
                                         max_length=SEQ_LEN) 
    
    token_ids = np.array(encoded_dict['input_ids']).reshape(1, -1) 
    token_masks = np.array(encoded_dict['attention_mask']).reshape(1, -1)
    token_segments = np.array(encoded_dict['token_type_ids']).reshape(1, -1)
    
    new_inputs = (token_ids, token_masks, token_segments)

    # Prediction
    prediction = model.predict(new_inputs)
    predicted_probability = np.round(np.max(prediction) * 100, 2) 
    # "분노":0, "놀람":1, "행복":2, "슬픔":3, "혐오":4,"공포":5 
    predicted_class = ["분노",'놀람', '행복',"슬픔","혐오","공포"][np.argmax(prediction, axis=1)[0]] 
    predicted_class_2 = ["분노",'놀람', '행복',"슬픔","혐오","공포"][np.argmax(prediction, axis=1)[1]] 
    
    print("첫번째 {}% 확률로 {} 리뷰입니다.".format(predicted_probability, predicted_class))
    print("두번째 {}% 확률로 {} 리뷰입니다.".format(predicted_probability, predicted_class_2))

In [ ]:
song="이윽고 내가 한눈에너를 알아봤을 때모든 건 분명 달라지고 있었어내 세상은 널 알기 전과 후로 나뉘어니가 숨 쉬면 따스한 바람이 불어와니가 웃으면 눈부신 햇살이 비춰거기 있어줘서 그게 너라서가끔 내 어깨에 가만히 기대주어서나는 있잖아 정말 빈틈없이 행복해너를 따라서 시간은 흐르고 멈춰물끄러미 너를 들여다 보곤 해그것 말고는 아무것도 할 수 없어서너의 모든 순간 그게나였으면 좋겠다생각만 해도 가슴이 차올라나는 온통 너로보고 있으면 왠지 꿈처럼 아득한 것몇 광년 동안 날 향해 날아온 별빛 또 지금의 너거기 있어줘서 그게 너라서가끔 나에게 조용하게 안겨주어서나는 있잖아 정말 남김없이 고마워너를 따라서 시간은 흐르고 멈춰물끄러미 너를 들여다보곤 해너를 보는 게 나에게는 사랑이니까너의 모든 순간 그게나였으면 좋겠다생각만 해도 가슴이 차올라나는 온통 너로니 모든 순간 나였으면"

In [ ]:
predict_sentiment(song, tokenizer, model)

INFO:absl:TPU has inputs with dynamic shapes: [<tf.Tensor 'Const:0' shape=() dtype=int32>, <tf.Tensor 'cond/Identity:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_8:0' shape=(None, 300) dtype=int64>, <tf.Tensor 'cond/Identity_16:0' shape=(None, 300) dtype=int64>]


59.44% 확률로 슬픔 리뷰입니다.


In [ ]:
song1="네가 없이 웃을 수 있을까생각만 해도 눈물이나힘든 시간 날 지켜준 사람이제는 내가 그댈 지킬 테니너의 품은 항상 따뜻했어고단했던 나의 하루에유일한 휴식처나는 너 하나로 충분해긴 말 안 해도 눈빛으로 다 아니깐한 송이의 꽃이 피고 지는모든 날 모든 순간 함께해햇살처럼 빛나고 있었지나를 보는 네 눈빛은꿈이라고 해도 좋을 만큼그 모든 순간은 눈부셨다불안했던 나의 고된 삶에한줄기 빛처럼 다가와날 웃게 해준 너나는 너 하나로 충분해긴 말 안 해도 눈빛으로 다 아니깐한 송이의 꽃이 피고 지는모든 날 모든 순간 함께해알 수 없는 미래지만네 품속에 있는 지금 순간 순간이영원 했으면 해갈게 바람이 좋은 날에햇살 눈부신 어떤 날에 너에게로처음 내게 왔던 그날처럼모든 날 모든 순간 함께해"

In [ ]:
predict_sentiment(song1, tokenizer, model)

82.97% 확률로 슬픔 리뷰입니다.


In [ ]:
song2="일부러 몇 발자국 물러나내가 없이 혼자 걷는 널 바라본다옆자리 허전한 너의 풍경흑백 거리 가운데 넌 뒤돌아본다그때 알게 되었어난 널 떠날 수 없단 걸우리 사이에 그 어떤 힘든 일도이별보단 버틸 수 있는 것들이었죠어떻게 이별까지 사랑"

In [ ]:
predict_sentiment(song2, tokenizer, model)

59.38% 확률로 슬픔 리뷰입니다.


In [ ]:
song3="너는 참 못됐다나 없이도 잘 지내더라 언제쯤 나도 널 잊을 수 있을까 눈을 감아도 눈물이 흐르고 어딜 가도 너만 보여 어느새 니가 없는긴 하루가 지나간다 다른 사람을 또 만나봐도 니가 아님 안 되겠어 울다가 또 웃다가 미친 것처럼 또 보고 싶다 상처 같은 널 잊어보려고 아무리 애를 써도너만 보고 싶다 니가 없인 아무것도 못 해 니가 없는 나는 아무것도 아냐 나도 참 못됐다 자꾸만 또 힘이 들더라 예전처럼 돌아갈 수가 있을까 눈을 감아도 니가 떠오르고 어딜 가도 너만 보여 자주 걷던 그 길 끝 저 너머 그댄 보일까요 다른 사람을 또 만나봐도 니가 아님 안 되겠어 울다가 또 웃다가 미친 것처럼 또 보고 싶다 상처 같은 널 잊어보려고 아무리 애를 써도 너만 보고 싶다니가"

In [ ]:
predict_sentiment(song3, tokenizer, model)

73.18% 확률로 슬픔 리뷰입니다.


In [ ]:
song4="오늘도 본을 떠 원효대사 해골물오 월 로제 미카사 아커만Don't worry 돈과 빛 재산 해결 못해정월대보름에 늑대야 에구머니나원효대사 오면 절이 엎어지고현역 대상 오 불합격추억팔이 은폐엄폐어우 연애는 나 못 해저기 오빠 또 해줘저녁에 소고기 쏴버려 엎어 지갑래원이는 원효대사 now잃어버린 대사관엔루머에 가린 패싸움 달인이름 모를 그 사나이피곤해 방콕해 직원 해방100원에 박혀있는 뜨거운 파편비구름 밖 지구 네 바퀴비굴의 파견 미군의 방패보아뱀 닮아버린 반 페르시부합해 루시퍼 베드신발포해 리스폰페르시아 완패를 시켜죽은 애들과 붉은 횃불빅원의 품은 포근해 woo량주 먹고 토해 알고 보니 해골물담주목금토일 like 거머리의 그물설총 사회적 파장 가져와서울 종각에 프란체스카Guess what카드 보안 필수 카르마 티리비두 팀이 비슷한 순간산송장 빌의 버저 비트스필버그 링컨 휘파람 비트 틀고NBA 번호 뒤에 달아부리나케 달아나파란 하늘 나무늘보나문희 호박 고구마필트오버 블리츠 how much겨울에 얼어버린 미토콘드리아아랍에미레이트 항공부익부 빈익빈미필이 부린 객기Fred Perry 구입뿔뿔이 대피구름 위를 걸으면 VIP그림을 그려봐 머피의 법칙또 본을 떠 원효대사 해골물오 월 로제 미카사 아커만Don't worry 돈과 빛재산 해결 못해정월대보름에 늑대야 에구머니나원효대사 오면 절이 엎어지고현역 대상 오 불합격추억팔이 은폐엄폐어우 연애는 나 못 해저기 오빠 또 해줘저녁에 소고기 쏴버려 엎어 지갑아빠 저금통 500원짜리누가 자꾸 털어 암행어사 필요해 치고 박고 싸워지구본이 손에 느껴져그토록 설레발 애써 네이버뒤져봐도 안 나오는 헛된 바램수원대 입구 앞에 벌어대 guap허파에 바람 들어가서 부활해어차피 떠나갈 새끼들 보임충고 때려 넣고 이어폰 꽂고 poem그대로 보여줘카톡으로 ㅋㅋ that point뻔하지 카테고리 똥글에 부워래원인 반칙 꼬라박지 rhyme shit영원히 갇힌 네 힙합이 나의 간식"

In [ ]:
predict_sentiment(song4, tokenizer, model)

62.43% 확률로 분노 리뷰입니다.
